# Directed and weighted graphs - a neurodynamic model of synchronization in the human brain

#### Topics covered in this tutorial include:
 * constructing a directed, weighted graph from data
 * some useful macros
 * parameter handling
 * stiff equations



## The FitzHugh-Nagumo model

Dynamics of spiking neurons have been described in a simplified manner by the [FitzHugh-Nagumo model](https://en.wikipedia.org/wiki/FitzHugh%E2%80%93Nagumo_model).

\begin{eqnarray}
 \varepsilon \dot u & = & u - u^3 - v \\
 \dot v & = &  u + a
\end{eqnarray}

Here $u$ is a fast, excitatory variable corresponding to the membrane potential and $v$ is a slower, inhibitory varibale. $\varepsilon$ is a parameter separating these time-scales, and $a$ is a control parameter.

In simplified models of the brain, such *relaxation oscillators* may be used to model individual neurons, clusters of neurons or even larger areas in the brain. The FitzHugh-Nagumo model has been widely used for studying synchronization in neuronal activity, which in turn has been connected to physiological phenomena such as epileptic seizures.

## Coupling relaxation oscillators

While different coupling schemes for FitzHugh-Nagumo oscillators have been proposed, in this tutorial we focus on coupling of the excitatory variables via electrical gap junctions, as described by the following system of equations.

\begin{eqnarray}
 \varepsilon \dot u_i & = & u_i - u_i^3 - v_i - \sigma \sum_{j=1}^N G_{ij}(u_i - u_j) \\
 \dot v_i & = &  u_i + a
\end{eqnarray}

This is a simple diffusive coupling mediated by the difference between activation potentials in pairs of neurons. A similar coupling term was introduced in the "getting started" tutorial.

## The network topology - a brain atlas

In the following we will use a directed and weigthed network encoding the strength and directionality of coupling between 90 different areas of the brain [[N.Tzourio-Mazoyer, 2002]](https://www.sciencedirect.com/science/article/abs/pii/S1053811901909784).

The network weight matrix is given as a text file containing 90 lines with 90 numbers representing the coupling strength and separated by commas `,`. The data can be conveniently read into a matrix with the `DelimitedFiles` module.





In [1]:
using DelimitedFiles

G = readdlm("git/NetworkDynamics.jl/examples/Norm_G_DTI.txt", ',', Float64, '\n');


The data structure for directed, weighted graphs is provided by the package `SimpleWeightedGraphs.jl` which is based on `LightGraphs.jl`.

In [2]:
using SimpleWeightedGraphs, LightGraphs

# First we construct a weighted, directed graph
g_weighted = SimpleWeightedDiGraph(G)

# For later use we extract the edge.weight attributes
# . is the broadcasting operator and gets the attribute :weight for every edge
edge_weights = getfield.(collect(edges(g_weighted)), :weight);

## Setting up the ODEProblem

Defining `VertexFunction` and `EdgeFunction` is similar to the example before. The macros `@inline` and `Base.@propagate_inbounds` give the compiler more freedom to compile efficient code. For more details see the julia [documentation](https://docs.julialang.org/en/v1/devdocs/boundscheck/).

In [3]:
using NetworkDynamics

@inline Base.@propagate_inbounds function fhn_electrical_vertex!(dv, v, e_s, e_d, p, t)
    dv[1] = v[1] - v[1]^3 / 3 - v[2]
    dv[2] = (v[1] - a) * ϵ
    for e in e_s
        dv[1] -= e[1]
    end
    for e in e_d
        dv[1] += e[1]
    end
    nothing
end

odeelevertex = ODEVertex(f! = fhn_electrical_vertex!, dim = 2, sym=[:u, :v]);

In [4]:
@inline Base.@propagate_inbounds function electrical_edge!(e, v_s, v_d, p, t)
    e[1] =  p * (v_s[1] - v_d[1]) # * σ
    nothing
end
electricaledge = StaticEdge(f! = electrical_edge!, dim = 1)

# Assembling the network

fhn_network! = network_dynamics(odeelevertex, electricaledge, g_weighted)


(::DiffEqBase.ODEFunction{true,nd_ODE_Static{SimpleWeightedDiGraph{Int64,Float64},Array{Float64,1},Array{Float64,1},ODEVertex{typeof(fhn_electrical_vertex!)},StaticEdge{typeof(electrical_edge!)}},LinearAlgebra.UniformScaling{Bool},Nothing,Nothing,Nothing,Nothing,Nothing,Nothing,Nothing,Nothing,Nothing,Array{Symbol,1},Nothing}) (generic function with 7 methods)

Note that the multiplication with the coupling strength $\sigma$ has been commented out. Since $\sigma$ is the same for every edge we can absorb this multiplication into the edge weight parameter `p`. Since our network has almost 8000 edges, this saves 8000 multiplications at every function call and leads to an 8-fold increase in performance. 

## Parameter handling

In [41]:
# Defining global parameters

N = 90       # number of nodes
ϵ = 0.05
a = .5
σ = .5

# Tuple of parameters for nodes and edges

p = (nothing, σ * edge_weights)

# Initial conditions

x0 = randn(2N) * 5;


The behaviour of `network_dynamics` changes with the type of parameters `p` being passed. When `p` is an `Array`, the entire Array will be passed to each `VertexFunction` and `EdgeFunction`. When `p` is a tuple of two Arrays with lengths corresponding to the number of nodes and number of edges respectively, then `network_dynamics` passes only the edge or node parameters with the index of the edge or node. When there are no parameters for either edges or nodes the value `nothing` may be used.

## Solving the system

Now we are ready to create an `ODEProblem`. Since for some choices of parameters the FitzHugh-Nagumo model is *stiff* (i.e. numerically unstable), we use a solver with automated stiffness detection. Such a solver switches to a more stable solver only when the solution enters a region of phase space where the problem is numerically unstable. In this case we use `Tsit5` and switch to `TRBDF2` when necessary. `AutoTsit5` is the switching version of the `Tsit5` algorithm.

In [42]:
using OrdinaryDiffEq

tspan = (0., 200.)
prob  = ODEProblem(fhn_network!, x0, tspan, p)
sol   = solve(prob, AutoTsit5(TRBDF2()));

## Plotting

The plot of the excitatory variables shows that they synchronize for this choice of parameters.

In [44]:
using Plots

plot( sol, vars = idx_containing(fhn_network!, :u), legend = false, ylim=(-5,5))

`Interact.jl` provides tools that allows to dynamically change inputs and observe the effect on the output of a program. In the example below we  study the effect of the coupling strength $\sigma$ on synchronization of the network.

In [28]:
using Interact

tspan = (0.,100.)

@manipulate for σ=10.0.^collect(-2:0.25:0.)
    p = (nothing, σ * edge_weights)
    prob = ODEProblem(fhn_network!, x0, tspan, p)
    sol = solve(prob, AutoTsit5(TRBDF2()), reltol = 1e-3) #low precision for faster solve
    plot( sol, vars = u_idx[1:20], tspan = tspan)
end

Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Scope(Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :label), Any["σ"], Dict{Symbol,Any}(:className => "interact ",:style => Dict{Any,Any}(:padding => "5px 10px 0px 10px")))], Dict{Symbol,Any}(:className => "interact-flex-row-left")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :input), Any[], Dict{Symbol,Any}(:max => 9,:min => 1,:attributes => Dict{Any,Any}(:type => "range",Symbol("data-bind") => "numericValue: index, valueUpdate: 'input', event: {change: function (){this.changes(this.changes()+1)}}","orient" => "horizontal"),:step => 1,:className => "slider slider is-fullwidth",:style => Dict{Any,Any}()))], Dict{Symbol,Any}(:className => "interact-flex-row-center")), Node{WebIO.DOM}(WebIO.DOM(:html, :div), Any[Node{WebIO.DOM}(WebIO.DOM(:html, :p), Any[], Dict{Symbol,Any}(:attributes => Dict("data-bind" => "text: formatted_val")))], Dict{Symbol,Any}(:className => "interact-flex-row-right"))], Dict{Symbol,Any}(:className => "interact-flex-row interact-widget")), Dict{String,Tuple{Observables.AbstractObservable,Union{Nothing, Bool}}}("changes" => (Observable{Int64} with 1 listeners. Value:
0, nothing),"index" => (Observable{Any} with 2 listeners. Value:
5, nothing)), Set(String[]), nothing, Asset[Asset("js", "knockout", "/home/micha/.julia/packages/Knockout/1sDlc/src/../assets/knockout.js"), Asset("js", "knockout_punches", "/home/micha/.julia/packages/Knockout/1sDlc/src/../assets/knockout_punches.js"), Asset("js", nothing, "/home/micha/.julia/packages/InteractBase/9mFwe/src/../assets/all.js"), Asset("css", nothing, "/home/micha/.julia/packages/InteractBase/9mFwe/src/../assets/style.css"), Asset("css", nothing, "/home/micha/.julia/packages/Interact/SbgIk/src/../assets/bulma_confined.min.css")], Dict{Any,Any}("changes" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"changes\"]()) ? (this.valueFromJulia[\"changes\"]=true, this.model[\"changes\"](val)) : undefined})")],"index" => Any[WebIO.JSString("(function (val){return (val!=this.model[\"index\"]()) ? (this.valueFromJulia[\"index\"]=true, this.model[\"index\"](val)) : undefined})")]), WebIO.ConnectionPool(Channel{Any}(sz_max:32,sz_curr:0), Set(AbstractConnection[]), Base.GenericCondition{Base.AlwaysLockedST}(Base.InvasiveLinkedList{Task}(Task (runnable) @0x00007f459870ba90, Task (runnable) @0x00007f459870ba90), Base.AlwaysLockedST(1))), WebIO.JSString[WebIO.JSString("function () {\n    var handler = (function (ko, koPunches) {\n    ko.punches.enableAll();\n    ko.bindingHandlers.numericValue = {\n        init: function(element, valueAccessor, allBindings, data, context) {\n            var stringified = ko.observable(ko.unwrap(valueAccessor()));\n            stringified.subscribe(function(value) {\n                var val = parseFloat(value);\n                if (!isNaN(val)) {\n                    valueAccessor()(val);\n                }\n            });\n            valueAccessor().subscribe(function(value) {\n                var str = JSON.stringify(value);\n                if ((str == \"0\") && ([\"-0\", \"-0.\"].indexOf(stringified()) >= 0))\n                     return;\n                 if ([\"null\", \"\"].indexOf(str) >= 0)\n                     return;\n                stringified(str);\n            });\n            ko.applyBindingsToNode(\n                element,\n                {\n                    value: stringified,\n                    valueUpdate: allBindings.get('valueUpdate'),\n                },\n                context,\n            );\n        }\n    };\n    var json_data = {\"formatted_vals\":[\"0.01\",\"0.0177828\",\"0.0316228\",\"0.0562341\",\"0.1\",\"0.177828\",\"0.316228\",\"0.562341\",\"1.0\"],\"changes\":WebIO.getval({\"name\":\"changes\",\"scope\":\"3120538513293057229\",\"id\":\"ob_12\",\"type\":\"observable\"}),\"index\":WebIO.getval({\"